In [1]:
#Trying to replicate the results of "Adaptive activation functions accelerate convergence in deep and physics-informed neural networks"
import torch
import torch.autograd as autograd         # computation graph
from torch import Tensor                  # tensor node in the computation graph
import torch.nn as nn                     # neural networks
import torch.optim as optim               # optimizers e.g. gradient descent, ADAM, etc.

import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
from mpl_toolkits.axes_grid1 import make_axes_locatable
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.ticker
from torch.nn.parameter import Parameter

import numpy as np
import time
from pyDOE import lhs         #Latin Hypercube Sampling
import scipy.io
from scipy.io import savemat

from smt.sampling_methods import LHS

#Set default dtype to float32
torch.set_default_dtype(torch.float)

#PyTorch random number generator
torch.manual_seed(1234)

# Random number generators in other libraries
np.random.seed(1234)

# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')

print(device)

if device == 'cuda': 
    print(torch.cuda.get_device_name())


cuda:0


In [2]:
def true_smooth(x): #[-3,3]
    term1 = (np.power(x,3) - x)
    term2 = np.sin(7*x)/7  
    
    term3 = np.sin(12*x)
    term12 = np.multiply(term1,term2)

    return term12  + term3

In [3]:
# Domain bounds
label = "Regr_smooth_Swish"
loss_thresh = 0.1

lb = np.array(-3.0)  # [-1. 0.]
ub = np.array(3.0) # [1.  0.99]

x_test = np.linspace(lb,ub,1000).reshape(-1,1)
u_true = true_smooth(x_test)

u_true_norm = np.linalg.norm(u_true,2)

In [4]:
def trainingdata(N_train,seed):
    np.random.seed(seed)
    
    x_train = np.random.uniform(low=lb, high=ub, size=(N_train,)).reshape(-1,1)

    u_train = true_smooth(x_train)

    return x_train, u_train

In [5]:
class Sequentialmodel(nn.Module):
    
    def __init__(self,layers):
        super().__init__() #call __init__ from parent class 
              
        'activation function'
        self.activation = nn.Sigmoid()
     
        'loss function'
        self.loss_function = nn.MSELoss(reduction ='mean')
        
        'Initialise neural network as a list using nn.Modulelist'  
        self.linears = nn.ModuleList([nn.Linear(layers[i], layers[i+1]) for i in range(len(layers)-1)])
     
        
        for i in range(len(layers)-1):
            nn.init.xavier_normal_(self.linears[i].weight.data, gain=1.0)
            # set biases to zero
            nn.init.zeros_(self.linears[i].bias.data)

        
        self.beta = Parameter(torch.ones((layers[1],len(layers)-2)))
        self.beta.requiresGrad = True
            
            
    'foward pass'
    def forward(self,x):
        if torch.is_tensor(x) != True:         
            x = torch.from_numpy(x)                
        
        u_b = torch.from_numpy(ub).float().to(device)
        l_b = torch.from_numpy(lb).float().to(device)
                      
        #preprocessing input 
        x = (x - l_b)/(u_b - l_b) #feature scaling
        
        #convert to float
        a = x.float()
        
        for i in range(len(layers)-2):
            z = self.linears[i](a)
            a = self.activation(z) + self.beta[:,i]*z*self.activation(z)
    
        a = self.linears[-1](a) 
        
        return a
    
    
    def loss(self,x,u):

        loss_val = self.loss_function(self.forward(x),u)
        
        return loss_val
        
    'test neural network'
    def test(self):
        u_pred = self.forward(x_test_tensor)       
        u_pred = u_pred.cpu().detach().numpy()
        
        return u_pred
    
    def test_loss(self):
        u_pred = self.test()
        
        test_mse_loss = np.mean(np.square(u_pred.reshape(-1,1) - u_true.reshape(-1,1)))
        test_re_loss = np.linalg.norm(u_pred.reshape(-1,1) - u_true.reshape(-1,1),2)/u_true_norm
        
        return test_mse_loss, test_re_loss  

In [6]:
def data_update(loss_np):
    train_loss.append(loss_np)
    beta_val.append(model_NN.beta.cpu().detach().numpy())
    test_mse, test_re = model_NN.test_loss()
    test_mse_loss.append(test_mse)
    test_re_loss.append(test_re)

In [7]:
def train_step():
    optimizer.zero_grad()     # zeroes the gradient buffers of all parameters
    loss = model_NN.loss(x_train,u_train)
    loss.backward() #backprop
    optimizer.step()
    
    return loss

In [8]:
def train_model(max_iter,rep):
    print(rep) 
   
    torch.manual_seed(rep*123)
    start_time = time.time()
    thresh_flag = 0
    
    for i in range(max_iter):
        loss_np = train_step().cpu().detach().numpy()
        if(thresh_flag == 0):
            if(loss_np < loss_thresh):
                time_threshold[rep] = time.time() - start_time
                epoch_threshold[rep] = i+1            
                thresh_flag = 1
                
        data_update(loss_np)
        print(i,"Train Loss",train_loss[-1],"Test MSE",test_mse_loss[-1],"Test RE",test_re_loss[-1])
    
    elapsed_time[rep] = time.time() - start_time
    print('Training time: %.2f' % (elapsed_time[rep]))

In [ ]:
max_reps = 10
max_iter = 5000
layers = np.array([1,50,50,50,50,1])

train_loss_full = []
test_mse_full = []
test_re_full = []
beta_full = []
elapsed_time= np.zeros((max_reps,1))

time_threshold = np.empty((max_reps,1))
time_threshold[:] = np.nan
epoch_threshold = max_iter*np.ones((max_reps,1))


for reps in range(max_reps):
    
    train_loss = []
    test_mse_loss = []
    test_re_loss = []
    beta_val = []
    'Generate Training data'
    N_train = 300
    
    x_train_np_array, u_train_np_array = trainingdata(N_train,reps*1234)

    'Convert to tensor and send to GPU'
    x_train = torch.from_numpy(x_train_np_array).float().to(device)
    u_train = torch.from_numpy(u_train_np_array).float().to(device)
    
    x_test_tensor = torch.from_numpy(x_test).float().to(device)
       
     
    model_NN = Sequentialmodel(layers)
    model_NN.to(device)
    print(model_NN)
    params = list(model_NN.parameters())
    #optimizer = optim.Adam(PINN.parameters(), lr=0.0008,betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
    optimizer = optim.Adam(model_NN.parameters(), lr=0.0008)

    train_model(max_iter,reps)
 
    torch.save(model_NN.state_dict(),label+'_'+str(reps)+'.pt')
    train_loss_full.append(train_loss)
    test_mse_full.append(test_mse_loss)
    test_re_full.append(test_re_loss)
    beta_full.append(beta_val)
                 

mdic = {"train_loss": train_loss_full,"test_mse": test_mse_full, "test_re": test_re_full,"Time": elapsed_time, "Thresh_time": time_threshold, "epoch_thresh": epoch_threshold,"beta": beta_full, "label": label}
savemat(label+'.mat', mdic) 

Sequentialmodel(
  (activation): Tanh()
  (loss_function): MSELoss()
  (linears): ModuleList(
    (0): Linear(in_features=1, out_features=50, bias=True)
    (1): Linear(in_features=50, out_features=50, bias=True)
    (2): Linear(in_features=50, out_features=50, bias=True)
    (3): Linear(in_features=50, out_features=50, bias=True)
    (4): Linear(in_features=50, out_features=1, bias=True)
  )
)
0
0 Train Loss 1.4046812 Test MSE 1.4056323076893227 Test RE 1.000939157507277
1 Train Loss 1.3953683 Test MSE 1.4179159029477533 Test RE 1.0053031675181814
2 Train Loss 1.395787 Test MSE 1.4140196977536639 Test RE 1.0039210115494654
3 Train Loss 1.3915098 Test MSE 1.403253627674116 Test RE 1.000091879707301
4 Train Loss 1.3855621 Test MSE 1.3934236555738804 Test RE 0.9965828374767942
5 Train Loss 1.3814263 Test MSE 1.3873503399910523 Test RE 0.9944086345442112
6 Train Loss 1.3787458 Test MSE 1.384579424938288 Test RE 0.9934150862739847
7 Train Loss 1.3754848 Test MSE 1.384334159155389 Test RE 0

112 Train Loss 1.0571563 Test MSE 1.1931192060659046 Test RE 0.9221758242662661
113 Train Loss 1.0477374 Test MSE 1.160595953051322 Test RE 0.9095201814890731
114 Train Loss 1.0333096 Test MSE 1.1465858761132401 Test RE 0.9040138997753151
115 Train Loss 1.027089 Test MSE 1.164564089171192 Test RE 0.9110737024251493
116 Train Loss 1.0186615 Test MSE 1.1478457559377675 Test RE 0.9045104330908144
117 Train Loss 1.009041 Test MSE 1.12797980820575 Test RE 0.8966490174990794
118 Train Loss 1.0047524 Test MSE 1.1370169002385775 Test RE 0.9002337157016459
119 Train Loss 0.9960541 Test MSE 1.1392950735981773 Test RE 0.9011351368612949
120 Train Loss 0.9916046 Test MSE 1.1158928281420826 Test RE 0.8918320125098455
121 Train Loss 0.98588425 Test MSE 1.1151198542369998 Test RE 0.8915230750039315
122 Train Loss 0.9789429 Test MSE 1.123849762991494 Test RE 0.8950059929738031
123 Train Loss 0.9758086 Test MSE 1.1008456827839455 Test RE 0.8857986947241423
124 Train Loss 0.96824884 Test MSE 1.093015681

220 Train Loss 0.69974834 Test MSE 0.7664252275006229 Test RE 0.7391059694917389
221 Train Loss 0.6979767 Test MSE 0.7713475407697358 Test RE 0.7414755994921515
222 Train Loss 0.6962305 Test MSE 0.7638524105915103 Test RE 0.737864372261189
223 Train Loss 0.694868 Test MSE 0.7646409268337931 Test RE 0.7382451185679759
224 Train Loss 0.6935106 Test MSE 0.7657236223868343 Test RE 0.7387675938489265
225 Train Loss 0.6923625 Test MSE 0.7572888634905903 Test RE 0.734687412910783
226 Train Loss 0.69161487 Test MSE 0.7668311293319539 Test RE 0.7393016603076384
227 Train Loss 0.6907317 Test MSE 0.7538063824837472 Test RE 0.7329961935505757
228 Train Loss 0.6896552 Test MSE 0.7629973799737814 Test RE 0.7374512863880236
229 Train Loss 0.688301 Test MSE 0.7531539022219974 Test RE 0.7326788911911642
230 Train Loss 0.68724054 Test MSE 0.7583411993620212 Test RE 0.7351977000367683
231 Train Loss 0.68567413 Test MSE 0.7500715137011127 Test RE 0.7311780581982468
232 Train Loss 0.6840744 Test MSE 0.7548

328 Train Loss 0.5810172 Test MSE 0.624987616485387 Test RE 0.6674327612029954
329 Train Loss 0.57993066 Test MSE 0.6211685427312407 Test RE 0.6653904160564299
330 Train Loss 0.57877433 Test MSE 0.6205393539192687 Test RE 0.665053339847861
331 Train Loss 0.5776858 Test MSE 0.6194575109367223 Test RE 0.6644733628141051
332 Train Loss 0.57674134 Test MSE 0.6168636016967133 Test RE 0.6630806993293393
333 Train Loss 0.57591605 Test MSE 0.6177275471754997 Test RE 0.6635448741728212
334 Train Loss 0.57513624 Test MSE 0.61429591161026 Test RE 0.6616992260339146
335 Train Loss 0.5743418 Test MSE 0.6153332281442656 Test RE 0.6622576719020553
336 Train Loss 0.57347894 Test MSE 0.6115846563177654 Test RE 0.6602373740069215
337 Train Loss 0.572559 Test MSE 0.6124072632456105 Test RE 0.6606812482331744
338 Train Loss 0.5715741 Test MSE 0.6088978762305212 Test RE 0.6587855184329311
339 Train Loss 0.57056695 Test MSE 0.6095842056403536 Test RE 0.6591566944175199
340 Train Loss 0.56954265 Test MSE 0.6

433 Train Loss 0.49824658 Test MSE 0.5061617701510366 Test RE 0.6006430888522049
434 Train Loss 0.49547476 Test MSE 0.5041954604766243 Test RE 0.5994752808118275
435 Train Loss 0.4905473 Test MSE 0.5034532136354826 Test RE 0.5990338622058134
436 Train Loss 0.48910645 Test MSE 0.5002334135303234 Test RE 0.597115249941006
437 Train Loss 0.49117494 Test MSE 0.508085226675576 Test RE 0.6017832533683231
438 Train Loss 0.4921222 Test MSE 0.4979339234225712 Test RE 0.5957412491810894
439 Train Loss 0.48985094 Test MSE 0.5036824635870234 Test RE 0.5991702332234349
440 Train Loss 0.48724377 Test MSE 0.49663307282603936 Test RE 0.5949625543212264
441 Train Loss 0.4878947 Test MSE 0.5080196131858117 Test RE 0.601744395345979
442 Train Loss 0.49107015 Test MSE 0.4988865875769856 Test RE 0.5963108730872282
443 Train Loss 0.49283865 Test MSE 0.5098408507850885 Test RE 0.602822049667971
444 Train Loss 0.4901993 Test MSE 0.491845286285797 Test RE 0.5920877433962488
445 Train Loss 0.4859948 Test MSE 0.

...

3109 Train Loss 0.046250757 Test MSE 0.06636298842521211 Test RE 0.21748774059993398
3110 Train Loss 0.04630077 Test MSE 0.06565250629803351 Test RE 0.21632039596326622
3111 Train Loss 0.046244893 Test MSE 0.06579840299252705 Test RE 0.21656062225556763
3112 Train Loss 0.046056565 Test MSE 0.06556401217040482 Test RE 0.21617455583482087
3113 Train Loss 0.04592226 Test MSE 0.06547580605112073 Test RE 0.21602909237423043
3114 Train Loss 0.045920487 Test MSE 0.06570974027147379 Test RE 0.2164146663829918
3115 Train Loss 0.04592443 Test MSE 0.06521679260341529 Test RE 0.21560137800021073
3116 Train Loss 0.0458353 Test MSE 0.0656662937405707 Test RE 0.21634310909812832
3117 Train Loss 0.04571809 Test MSE 0.06496090806529238 Test RE 0.215177995627638
3118 Train Loss 0.045655 Test MSE 0.06551933975715828 Test RE 0.21610089740314323
3119 Train Loss 0.045615215 Test MSE 0.06509381273456696 Test RE 0.21539800138778736
3120 Train Loss 0.045538943 Test MSE 0.06497865410310197 Test RE 0.21520738481

3221 Train Loss 0.055457868 Test MSE 0.09512621490787126 Test RE 0.2603885735152161
3222 Train Loss 0.067944735 Test MSE 0.07015376918633698 Test RE 0.2236131394406517
3223 Train Loss 0.056746677 Test MSE 0.06206067511889073 Test RE 0.21031975250910417
3224 Train Loss 0.04113678 Test MSE 0.06684417337215982 Test RE 0.21827479684623965
3225 Train Loss 0.04369591 Test MSE 0.0684232015626745 Test RE 0.2208378497285849
3226 Train Loss 0.055241827 Test MSE 0.07970019650323663 Test RE 0.2383425109165605
3227 Train Loss 0.054618098 Test MSE 0.060279930301122164 Test RE 0.20728037465084329
3228 Train Loss 0.04337319 Test MSE 0.05805554871682653 Test RE 0.20342001467020784
3229 Train Loss 0.03978878 Test MSE 0.0705961432372618 Test RE 0.2243170588331621
3230 Train Loss 0.046806622 Test MSE 0.06467465964834429 Test RE 0.21470338431283226
3231 Train Loss 0.05022254 Test MSE 0.06708084223571598 Test RE 0.21866086791552886
3232 Train Loss 0.044330865 Test MSE 0.05850454002558403 Test RE 0.204205106

3326 Train Loss 0.034118798 Test MSE 0.052601660864843976 Test RE 0.19362950832718745
3327 Train Loss 0.034063786 Test MSE 0.05260003403485326 Test RE 0.19362651408022227
3328 Train Loss 0.034008846 Test MSE 0.052465889218586755 Test RE 0.1933794555466885
3329 Train Loss 0.03395386 Test MSE 0.05245392387039745 Test RE 0.19335740327146894
3330 Train Loss 0.03389854 Test MSE 0.05234467794606155 Test RE 0.19315594533798353
3331 Train Loss 0.03384307 Test MSE 0.05229749336131022 Test RE 0.19306886831085698
3332 Train Loss 0.033787474 Test MSE 0.05222430596401823 Test RE 0.19293372650834353
3333 Train Loss 0.033731956 Test MSE 0.05214227454350286 Test RE 0.19278214146407913
3334 Train Loss 0.033676304 Test MSE 0.05209789081910669 Test RE 0.19270007550997345
3335 Train Loss 0.033620726 Test MSE 0.05199665650729714 Test RE 0.19251276134865572
3336 Train Loss 0.033565283 Test MSE 0.051961748326473295 Test RE 0.19244812836035452
3337 Train Loss 0.033509597 Test MSE 0.051858560106194614 Test RE 

3426 Train Loss 0.038144693 Test MSE 0.053035113053404095 Test RE 0.19442565184907348
3427 Train Loss 0.037912447 Test MSE 0.051149107208933293 Test RE 0.19093732902191932
3428 Train Loss 0.03456173 Test MSE 0.04986020062153043 Test RE 0.18851626428673643
3429 Train Loss 0.031094002 Test MSE 0.049856699407233154 Test RE 0.1885096453058759
3430 Train Loss 0.03474159 Test MSE 0.05564190549805275 Test RE 0.19914656111219775
3431 Train Loss 0.03723894 Test MSE 0.04819766783050548 Test RE 0.18534668646810998
3432 Train Loss 0.031581994 Test MSE 0.045800490024285 Test RE 0.1806786664631517
3433 Train Loss 0.029165905 Test MSE 0.051383679468530896 Test RE 0.1913746520750025
3434 Train Loss 0.033642028 Test MSE 0.049493435927247816 Test RE 0.18782163483205314
3435 Train Loss 0.03396403 Test MSE 0.047980566642547705 Test RE 0.1849287782682657
3436 Train Loss 0.029936295 Test MSE 0.04588253416491119 Test RE 0.18084042230158473
3437 Train Loss 0.029650778 Test MSE 0.04775547792512168 Test RE 0.18

3530 Train Loss 0.023502216 Test MSE 0.03877561637187935 Test RE 0.16624598643296376
3531 Train Loss 0.023449203 Test MSE 0.038706300952758024 Test RE 0.16609732903257807
3532 Train Loss 0.023396252 Test MSE 0.03864359498356829 Test RE 0.16596273188077967
3533 Train Loss 0.023343405 Test MSE 0.038566002442456185 Test RE 0.16579602973035226
3534 Train Loss 0.0232905 Test MSE 0.03851466248399946 Test RE 0.16568563721548582
3535 Train Loss 0.02323765 Test MSE 0.038427767378101586 Test RE 0.16549862531066475
3536 Train Loss 0.023185093 Test MSE 0.038376993872813174 Test RE 0.165389254881692
3537 Train Loss 0.023132462 Test MSE 0.03830231778871484 Test RE 0.16522826473312272
3538 Train Loss 0.02308006 Test MSE 0.03823185973451167 Test RE 0.16507622405496605
3539 Train Loss 0.023027841 Test MSE 0.03817793614663812 Test RE 0.16495976825997505
3540 Train Loss 0.022975719 Test MSE 0.03809530094358928 Test RE 0.1647811458726987
3541 Train Loss 0.02292362 Test MSE 0.03804386660931465 Test RE 0.16

In [ ]:
u_pred = model_NN.test()

In [ ]:
plt.plot(x_test,u_pred,'rx')
plt.plot(x_test,u_true,'b')

In [ ]:
a = 0
for i in range(10):
    a = a + test_loss_full[i][-1]
print(a/10)